In [3]:
import os
import numpy as np
import xarray as xr
from scipy import stats
from tqdm import tqdm

# Settings
RAW_DATA_DIR = r"data/raw"
PATCHES_DIR = r"data/sequences"
PATCH_SIZE = 32
STRIDE = 16
TIME_WINDOW = 10

# Define NaN tolerance per region (fallback is 0.4)
region_thresholds = {
    "NET": 0.85,
    "CQC": 0.8,
    "WET": 0.75,
}

variables = ["monthly_rain", "max_temp", "min_temp", "radiation", "spi_1", "consecutive_drought"]
FEATURE_VARS = variables[:-1]  # exclude 'consecutive_drought'

os.makedirs(PATCHES_DIR, exist_ok=True)

def extract_sequence_patches(region_file):
    ds = xr.open_dataset(os.path.join(RAW_DATA_DIR, region_file))
    region_name = region_file.split("_Combined_Consecutive.nc")[0]
    region_dir = os.path.join(PATCHES_DIR, region_name)
    os.makedirs(region_dir, exist_ok=True)

    nan_ratio_threshold = region_thresholds.get(region_name, 0.4)

    metadata_path = os.path.join(region_dir, "metadata.csv")
    with open(metadata_path, "w") as meta_file:
        meta_file.write("filename,lat,lon,t,label\n")

    # Pad small regions
    pad_lat = max(0, PATCH_SIZE - ds.sizes['lat'])
    pad_lon = max(0, PATCH_SIZE - ds.sizes['lon'])

    ds = ds.pad(
        lat=(0, pad_lat),
        lon=(0, pad_lon),
        constant_values=np.nan
    )

    total_sequences, saved_sequences, skipped_nan = 0, 0, 0

    for lat in range(0, ds.sizes['lat'], STRIDE):
        for lon in range(0, ds.sizes['lon'], STRIDE):
            for t in range(0, ds.sizes['time'] - TIME_WINDOW + 1):
                patch_seq_raw = []

                for var in variables:
                    data_slice = ds[var].isel(
                        time=slice(t, t + TIME_WINDOW),
                        lat=slice(lat, lat + PATCH_SIZE),
                        lon=slice(lon, lon + PATCH_SIZE)
                    ).values
                    patch_seq_raw.append(data_slice)

                patch_seq_raw = np.stack(patch_seq_raw, axis=-1)  # (T, H, W, C)
                patch = np.full((TIME_WINDOW, PATCH_SIZE, PATCH_SIZE, len(variables)), np.nan)
                patch[:, :patch_seq_raw.shape[1], :patch_seq_raw.shape[2], :] = patch_seq_raw

                # Split features and label
                data_patch = patch[:, :, :, :-1]  # shape: (T, 32, 32, 5)
                label_patch = patch[-1, :, :, -1]  # final timestep, drought mask

                # === Skip if too much NaN ===
                nan_ratio = np.isnan(data_patch).mean()
                if nan_ratio > nan_ratio_threshold:
                    skipped_nan += 1
                    print(f"⛔ Skipped ({region_name}) lat={lat} lon={lon} t={t} — NaN ratio: {nan_ratio:.2f}")
                    continue

                # === Generate mask ===
                mask_patch = (~np.isnan(data_patch)).astype(np.float32)  # 1 = valid, 0 = NaN
                data_patch = np.nan_to_num(data_patch, nan=0.0)

                # Combine features + masks along channel axis
                final_patch = np.concatenate([data_patch, mask_patch], axis=-1)  # shape: (T, 32, 32, 10)
                final_patch = final_patch.astype(np.float32)

                # === Label: mode of valid values ===
                valid_vals = label_patch[~np.isnan(label_patch)]
                if len(valid_vals) == 0:
                    continue

                label = stats.mode(valid_vals.flatten(), nan_policy='omit', keepdims=False).mode
                if np.isnan(label) or label is None:
                    continue

                label = int(label >= 1)  # binarize

                # === Save ===
                outname = f"{region_name}_lat{lat}_lon{lon}_t{t}"
                np.save(os.path.join(region_dir, outname + ".npy"), final_patch)
                np.save(os.path.join(region_dir, outname + "_label.npy"), label)

                with open(metadata_path, "a") as meta_file:
                    meta_file.write(f"{outname}.npy,{lat},{lon},{t},{label}\n")

                saved_sequences += 1
                total_sequences += 1

    print(f"✅ {region_name}: Total = {total_sequences}, Saved = {saved_sequences}, Skipped (NaN) = {skipped_nan}")

if __name__ == "__main__":
    for file in tqdm(os.listdir(RAW_DATA_DIR)):
        if file.endswith("_Combined_Consecutive.nc"):
            extract_sequence_patches(file)


  0%|          | 0/13 [00:00<?, ?it/s]

⛔ Skipped (BRB) lat=0 lon=0 t=0 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=1 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=2 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=3 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=4 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=5 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=6 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=7 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=8 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=9 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=10 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=11 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=12 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=13 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=14 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=15 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=16 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=17 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=18 — NaN ratio: 0.96
⛔ Skipped (BRB) lat=0 lon=0 t=19 — NaN ra

  8%|▊         | 1/13 [01:40<20:00, 100.06s/it]

⛔ Skipped (CHC) lat=0 lon=0 t=0 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=1 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=2 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=3 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=4 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=5 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=6 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=7 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=8 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=9 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=10 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=11 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=12 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=13 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=14 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=15 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=16 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=17 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=18 — NaN ratio: 1.00
⛔ Skipped (CHC) lat=0 lon=0 t=19 — NaN ra

 15%|█▌        | 2/13 [02:46<14:41, 80.15s/it] 

...

⛔ Skipped (SEQ) lat=0 lon=0 t=0 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=1 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=2 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=3 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=4 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=5 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=6 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=7 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=8 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=9 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=10 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=11 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=12 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=13 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=14 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=15 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=16 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=17 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=18 — NaN ratio: 0.77
⛔ Skipped (SEQ) lat=0 lon=0 t=19 — NaN ra

 92%|█████████▏| 12/13 [09:32<00:35, 35.74s/it]

⛔ Skipped (SEQ) lat=96 lon=48 t=223 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=224 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=225 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=226 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=227 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=228 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=229 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=230 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=231 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=232 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=233 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=234 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=235 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=236 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=237 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=238 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=239 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=48 t=240 — NaN ratio: 1.00
⛔ Skipped (SEQ) lat=96 lon=4

100%|██████████| 13/13 [09:50<00:00, 45.44s/it]

⛔ Skipped (WET) lat=64 lon=32 t=155 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=156 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=157 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=158 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=159 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=160 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=161 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=162 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=163 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=164 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=165 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=166 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=167 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=168 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=169 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=170 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=171 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=32 t=172 — NaN ratio: 1.00
⛔ Skipped (WET) lat=64 lon=3